Integrating Numba with C - using CFFI
=====================================

This notebook gives an introduction to using CFFI to integrate Numba in C.

for more examples and information:
https://numba.pydata.org/numba-doc/latest/user/cfunc.html
https://github.com/numba/numba/blob/master/examples/notebooks/Accessing%20C%20Struct%20Data.ipynb


In [16]:
# dependencies:
import numba as nb
from cffi import FFI
import numpy as np

In [2]:
# example taken from the Numba documentation
ffi = FFI()

ffi.cdef("""
  double sin(double x);
""")

C = ffi.dlopen(None)
sin = C.sin

In [3]:
# CFFI wraps the sin function, so we can call it from python:
# there's however a significant overhead
%timeit sum([sin(x) for x in np.linspace(0, np.pi * 2, 100)])

1000 loops, best of 3: 96.4 µs per loop


In [4]:
# we can do the same with numba
@nb.njit()
def test1():
    lst = np.array([sin(x) for x in np.linspace(0, np.pi*2, 100)])
    return np.sum(lst)

In [5]:
# This will be much faster as numba is able to call the C-function directly.
np.testing.assert_almost_equal(test1(), 0)
%timeit test1()

100000 loops, best of 3: 3.8 µs per loop


In [6]:
# Of course, we could also use CFFI to do this from C:
ffi = FFI()

ffi.set_source("_sin", """
# include <stdlib.h>
#define _USE_MATH_DEFINES 
# include <math.h>

double sum(int n){
    double s, x = 0.;
    double stop = 2 * M_PI;
    double step = 2 * M_PI / (n * 1.);
    while(x < stop) {
        s += sin(x);
        x = x + step;
    }
    return s;
}

""")

ffi.cdef("""
double sum(int n);
""")

ffi.compile()

'C:\\workspace\\fosdem_2019\\_sin.pyd'

In [7]:
from _sin import lib
_sum = lib.sum
# this will be a bit faster, but same magnitude
%timeit _sum(100)

The slowest run took 5.61 times longer than the fastest. This could mean that an intermediate result is being cached.
100000 loops, best of 3: 3.26 µs per loop


Using numba.cfunc to call numba functions from C
================================================

When you use cfunc to created a JITed function, you can access the address of the underlying C-function.
You can then pass this pointer to another C-function to invoke it

In [8]:
from numba import cfunc

@cfunc("int64(int64)")
def mul_3(x):
    return x * 3

In [9]:
# the address:
mul_3.address

136470544L

In [10]:
# Now we can make a function that takes the pointer as an argument and 
# invoke it from C
ffi = FFI()

ffi.set_source("_func_invocation", """
typedef int (* my_func_t)(int);

int invoke_func(long func_ptr, int n){
    my_func_t my_func;
    my_func = (my_func_t) func_ptr;
    return my_func(n);
} 
""")

ffi.cdef("""
int invoke_func(long func_ptr, int n);
""")

ffi.compile()

'C:\\workspace\\fosdem_2019\\_func_invocation.pyd'

In [11]:
from _func_invocation.lib import invoke_func

In [12]:
invoke_func(mul_3.address, 2)

6

In [13]:
@cfunc("int64(int64)")
def mul_4(x):
    return x * 4

In [14]:
invoke_func(mul_4.address, 2)

8

Numpy C-interopability
======================

Numpy is great, it provides some utilities to make it easier to access and manipulate the data
from C.

In [15]:
from numba.types import void, CPointer, complex64, intp, char
from numpy import ctypeslib
import numpy as np
import numba as nb

@nb.njit()
def calculate_smatrix(smat):
    reflection = 0.4
    for idx in range(smat.shape[0]):
        smat[idx, idx] = reflection

@nb.cfunc(nb.types.void(CPointer(nb.types.complex128), intp))
def fill_smat(ar_ptr, n):
    ar = nb.carray(ar_ptr, (n, n))
    calculate_smatrix(ar)


n = 4
ar_np = np.zeros((n, n), dtype=np.complex128)
ar_c = ar_np.ctypes.data_as(ctypeslib.ndpointer(np.complex128, ndim=1, flags='C'))
fill_smat.ctypes(ar_c, n)
print(ar_np)


[[ 0.4+0.j  0.0+0.j  0.0+0.j  0.0+0.j]
 [ 0.0+0.j  0.4+0.j  0.0+0.j  0.0+0.j]
 [ 0.0+0.j  0.0+0.j  0.4+0.j  0.0+0.j]
 [ 0.0+0.j  0.0+0.j  0.0+0.j  0.4+0.j]]
